# Inspecting the SRRL weather data and the pyranometer data
The SRRL data and the pyranometer data will be plotted to determine the sunniest period for BR modeling of the irradiance distribution at the BARN facility at NREL Golden campus.

In [1]:
# First, load the packages
import os
from pathlib import Path
import numpy as np
import pandas as pd
import bifacial_radiance as br

# This information helps with debugging and getting support :)
import sys, platform
print("Working on a ", platform.system(), platform.release())
print("Python version ", sys.version)
print("Pandas version ", pd.__version__)

Working on a  Windows 10
Python version  3.11.5 | packaged by Anaconda, Inc. | (main, Sep 11 2023, 13:26:23) [MSC v.1916 64 bit (AMD64)]
Pandas version  2.0.3


## Data wrangling
### SRRL data
1. Create a datetime variable and set it as the index
2. Change the data to a tidy form (until I can figure out how to work with plotly in a long form)

### Measured pyranometer data
1. Create a datetime variable and set it as the index
2. Change the data to a tidy form

In [2]:
# Load the measured data
measured = pd.read_csv(os.path.join(os.path.join(Path().resolve(), 'Data','BARNirrad_measured.csv')), header = 1) # The field pyranometer data
srrl_weather = pd.read_csv(str(Path().resolve() / 'WeatherFiles' /  'PSM3_15T.csv'), header = 2) # Data from SRRL

## SRRL data
# Create a Datetime variable and set it as the index
srrl_weather['date'] = srrl_weather[['Year','Month','Day']].astype(str).agg('-'.join, axis=1) # Couldn't think of a proper way to chain this process into a single command. If you think of something, please let me know
srrl_weather['time'] = srrl_weather[['Hour','Minute']].astype(str).agg(':'.join, axis=1)
srrl_weather['Datetime'] = pd.to_datetime(srrl_weather[['date','time']].agg(" ".join, axis=1))
srrl_weather.set_index('Datetime', inplace=True)

## Measured pyranometer data
# Create a Datetime variable for the measured data using the existing 'TIMESTAMP' column.
measured['Datetime'] = pd.to_datetime(measured['TIMESTAMP'], format ='%m/%d/%Y %H:%M')
measured = measured.drop(["TIMESTAMP", "RECORD"], axis = 'columns') # drop this column so the resample command does not confuse TIMESTAMP and Datetime columns

measured = measured.set_index('Datetime').resample('15T', axis = 'index', label='left', closed='right').mean() # The "label" and the "closed" arguments are different from that of how the SRRL data was read-in (which was "right" for both arguments), but this somehow yields a better timing match.

## Join two datasets
srrlandmeasured = pd.concat([srrl_weather, measured], axis = 1, join = 'inner')


In [3]:
import plotly.express as px
import plotly.graph_objects as go

In [4]:
fig1 = px.line(srrlandmeasured.reset_index(), x = 'Datetime', y = ['GHI', 'DNI'])
fig1.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "15-min average irradiance (W/m<sup>2</sup>)",
    legend=dict(
        yanchor="top",
        y=1.2,
        xanchor="center",
        x=0.5
    ),
    legend_title=dict(
        text = "Irradiance type"
    ),
    legend_orientation="h"
)
fig1.show()


# fig2 = px.line(snowlessdays.reset_index(), x = 'Datetime', y = ['Ap_1', 'Ap_2', 'Ap_3', "Ap_4", "Ap_5"])
fig2 = px.line(srrlandmeasured.reset_index(), x = 'Datetime', y = ['Ap_1', 'Ap_2', 'Ap_3', "Ap_4", "Ap_5"], facet_row= "variable")
fig2.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "15-min average irradiance (W/m<sup>2</sup>)",
    legend=dict(
        yanchor="top",
        y=1.2,
        xanchor="center",
        x=0.5
    ),
    legend_title=dict(
        text = "Sensor location"
    ),
    legend_orientation="h"
)
fig2.show()

fig3 = px.line(srrlandmeasured.reset_index(), x = 'Datetime', y = 'Albedo')
fig3.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "Albedo (Unitless)"
    )
fig3.show()

fig3 = px.line(srrlandmeasured.reset_index(), x = 'Datetime', y = 'Tdry')
fig3.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "Dry bulb temperature (°C)"
    )
fig3.show()

Sunny days for SRRL data

September: 8th, 16th, 17th, 22nd, 24-28th

October: 5th, 7th-8th, 13th, 15th-17th, 19th-20th, 22nd, 25th, 31st

Sunny days for SRRL and pyranometer data

September: 8th, 22nd, 25-28th

October: 5th, 7th-8th, 13th, 15th-17th, 19th-20th, 22nd, 25th, 31st

### Snowy days still need to be dropped
Upon visual inspection of the albedo, threshold value of snowy ground was set to 0.4

In [6]:
# Removing snowy days

snowydays = srrlandmeasured.groupby(pd.Grouper(freq='D')).max()[srrlandmeasured.groupby(pd.Grouper(freq='D')).max()['Albedo'] > 0.4] # Summarize to daily maximum albedo and choose all that exceed 0.4. Just for sanity check and cross-referencing with the albedo time series above.

snowlessdays = srrlandmeasured.reset_index().set_index(['Year', 'Month', 'Day'])[srrlandmeasured.groupby(pd.Grouper(freq='D')).max().reset_index().set_index(['Year', 'Month', 'Day'])['Albedo'] <= 0.4].reset_index().set_index('Datetime') # change the index of the original combined dataset from datetime to the joined year, month, and date columns, and use the same approach as above for "snowydays" to select the days with maximum albedo <= 0.4. Then set the index of the subset of the data to the year, month, and day columns as well to avoid index alignment issues.

print(snowydays)

            Year  Month  Day  Hour  Minute      Wspd       Tdry         DHI  \
Datetime                                                                      
2023-09-10  2023      9   10    23      45  3.047667  17.390000  395.302067   
2023-09-11  2023      9   11    23      45  2.436600  18.412000  475.571467   
2023-09-14  2023      9   14    23      45  4.407533  21.407333  481.696533   
2023-09-19  2023      9   19    23      45  6.692200  24.727333  303.816867   
2023-10-09  2023     10    9    23      45  3.778400  25.020000  147.617000   
2023-10-10  2023     10   10    23      45  5.133933  24.455333  243.886933   
2023-10-11  2023     10   11    23      45  8.005933  22.540000  369.231267   
2023-10-20  2023     10   20    23      45  4.279067  28.891333   52.944227   
2023-10-21  2023     10   21    23      45  3.487600  25.209333  145.414067   
2023-10-23  2023     10   23    23      45  4.038333  25.908667  189.528000   
2023-10-24  2023     10   24    23      45  3.299333

C:\Users\cchoi2\AppData\Local\Temp\1\ipykernel_3248\2461614524.py:5: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



In [7]:
fig5 = px.line(snowlessdays.reset_index(), x = 'Datetime', y = ['GHI', 'DNI'])
fig5.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "15-min average irradiance (W/m<sup>2</sup>)",
    legend=dict(
        yanchor="top",
        y=1.2,
        xanchor="center",
        x=0.5
    ),
    legend_title=dict(
        text = "Irradiance type"
    ),
    legend_orientation="h"
)
fig5.show()


# fig2 = px.line(srrlandmeasured.reset_index(), x = 'Datetime', y = ['Ap_1', 'Ap_2', 'Ap_3', "Ap_4", "Ap_5"])
fig6 = px.line(snowlessdays.reset_index(), x = 'Datetime', y = ['Ap_1', 'Ap_2', 'Ap_3', "Ap_4", "Ap_5"], facet_row= "variable")
fig6.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "15-min average irradiance (W/m<sup>2</sup>)",
    legend=dict(
        yanchor="top",
        y=1.2,
        xanchor="center",
        x=0.5
    ),
    legend_title=dict(
        text = "Sensor location"
    ),
    legend_orientation="h"
)
fig6.show()

fig7 = px.line(snowlessdays.reset_index(), x = 'Datetime', y = 'Albedo')
fig7.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "Albedo (Unitless)"
    )
fig7.show()

fig8 = px.line(snowlessdays.reset_index(), x = 'Datetime', y = 'Tdry')
fig8.update_layout(
    plot_bgcolor='white',
    xaxis_title = "",
    yaxis_title = "Dry bulb temperature (°C)"
    )
fig8.show()

Upon visual inspection, September 20th to 29th provides the longest period of sunny days with daily max albedo less than 0.4.

In [21]:

daysformodeling = srrlandmeasured.reset_index().loc[(srrlandmeasured.reset_index()['Datetime'] >= '2023-9-20') & (srrlandmeasured.reset_index()['Datetime'] <= '2023-09-29')]
daysformodeling = daysformodeling.set_index('Datetime')
